## **<h1 align="center"> Recommender systems on Netflix prize dataset</h1>**


## Table of Contents

- [1 - Packages](#1)
- [2 - Load Netflix Prize Data](#2)
    - [2 - 1  Load User-Data and Preprocessing](#ex-1)
    - [2 - 2  Load Movie-Data and Preprocessing](#ex-2)
- [3 - Exploratory Data Analysis (EDA)](#3)
- [4 - Create Train- and Testset](#4)
- [5 - Creating Sparse Matrix](#5)
- [6 - Recommendation Engines](#6)
    - [6 - 1  Cosine Similarity](ex-3)
    - [6 - 2  Autoencoders (AutoRec)](#ex-4)
    - [6 - 3  Matrix Factorisation](#ex-5)
    - [6 - 4  Deep Learning With Keras](#ex-6)
    - [6 - 5  Residual Learning](#ex-7)


In [1]:
! pip install kaggle                 # Install the Kaggle library
! mkdir ~/.kaggle                    # Make a directory named “.kaggle”
! cp kaggle.json ~/.kaggle/          # Copy the “kaggle.json” into this new directory
! chmod 600 ~/.kaggle/kaggle.json    # Allocate the required permission for this file
! kaggle datasets download netflix-inc/netflix-prize-data
! unzip netflix-prize-data

 97% 664M/683M [00:05<00:00, 119MB/s]
100% 683M/683M [00:05<00:00, 126MB/s]
Archive:  netflix-prize-data.zip
  inflating: README                  
  inflating: combined_data_1.txt     
  inflating: combined_data_2.txt     
  inflating: combined_data_3.txt     
  inflating: combined_data_4.txt     
  inflating: movie_titles.csv        
  inflating: probe.txt               
  inflating: qualifying.txt          


<a name='1'></a>
## 1 - Packages

In [1]:
import pandas as pd
import numpy as np
import tensorflow as tf

from pandas.api.types import CategoricalDtype

from plotly.offline import init_notebook_mode, plot, iplot
import plotly.offline as pyo
from plotly.subplots import make_subplots
import plotly.graph_objs as go
import plotly.io as pio
pio.renderers.default = "svg"
init_notebook_mode(connected=True)

from collections import deque

from sklearn.metrics import mean_squared_error
from sklearn.metrics.pairwise import cosine_similarity

import tensorflow.keras.backend as K
from tensorflow.keras.regularizers import l2
from tensorflow.keras.layers import Input, Embedding, Dot, Add, Flatten, Reshape, Concatenate, Dense, Dropout, BatchNormalization, Activation
from tensorflow.keras.optimizers import SGD, Adam
from tensorflow.keras.models import Model

from scipy import sparse
from scipy.sparse import csr_matrix, coo_matrix
from scipy.sparse import vstack

import os
from datetime import datetime

<a name='2'></a>
## 2 - Load Netflix Prize Data

<a name='ex-1'></a>

### 2 - 1 Load User-Data and Preprocessing

In [3]:
start = datetime.now()
if not os.path.isfile('data.csv'):
    # Create a file 'data.csv' before reading it
    # Read all the files in netflix and store them in one big file('data.csv')
    # reading from each of the four files and appending each rating to a global file 'train.csv'
    data = open('data.csv', mode='w')
    
    row = list()
    files=['/content/combined_data_1.txt','/content/combined_data_2.txt', 
           '/content/combined_data_3.txt', '/content/combined_data_4.txt']
    for file in files:
        print("Reading ratings from {}...".format(file))
        with open(file) as f:
            for line in f: 
                del row[:]
                line = line.strip()
                if line.endswith(':'):
                    # All below are ratings for this movie, until another movie appears.
                    movie_id = line.replace(':', '')
                else:
                    row = [x for x in line.split(',')]
                    row.insert(0, movie_id)
                    data.write(','.join(row))
                    data.write('\n')
        print("Done.\n")
    data.close()
print('Time taken :', datetime.now() - start)

Reading ratings from /content/combined_data_1.txt...
Done.

Reading ratings from /content/combined_data_2.txt...
Done.

Reading ratings from /content/combined_data_3.txt...
Done.

Reading ratings from /content/combined_data_4.txt...
Done.

Time taken : 0:03:20.209571


In [2]:
print("creating the dataframe from data.csv file..")
df = pd.read_csv('data.csv', sep=',', 
                       names=['movie_id', 'user_id', 'rating', 'date'])
df.date = pd.to_datetime(df.date)
df.movie_id = df.movie_id - 1
df['rating'] = df['rating'].astype(float)
print('Done.\n')

creating the dataframe from data.csv file..
Done.



In [ ]:
df.head()

movie_id  user_id  rating       date
0         0  1488844     3.0 2005-09-06
1         0   822109     5.0 2005-05-13
2         0   885013     4.0 2005-10-19
3         0    30878     4.0 2005-12-26
4         0   823519     3.0 2004-05-03

In [ ]:
df.info()
# df['user_id'].describe()
# df['user_id'].nunique()
# df['user_id'].isna().sum()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100480507 entries, 0 to 100480506
Data columns (total 4 columns):
 #   Column    Dtype         
---  ------    -----         
 0   movie_id  int64         
 1   user_id   int64         
 2   rating    float64       
 3   date      datetime64[ns]
dtypes: datetime64[ns](1), float64(1), int64(2)
memory usage: 3.0 GB


In [ ]:
dup_bool = df.duplicated(['movie_id','user_id','rating'])
duplicates = sum(dup_bool) # by considering all columns..( including timestamp)
print("There are {} duplicate rating entries in the data..".format(duplicates))

There are 0 duplicate rating entries in the data..


> **Note:** movie_ids are ordered sequentially from 1..17770, with no missing numbers - user_ids are integers from 6..2649429000, with no missing numbers

<a name='ex-2'></a>
### 2 - 2  Load Movie-Data and Preprocessing

In [3]:
movie_titles = pd.read_csv('./Data/movie_titles.csv', 
                           encoding = 'ISO-8859-1', 
                           header = None, 
                           names = ['movie_id', 'Year', 'movie_name'])

print('Shape Movie-Titles:\t{}'.format(movie_titles.shape))
movie_titles.movie_id = movie_titles.movie_id - 1
movie_titles.head()

Shape Movie-Titles:	(17770, 3)


movie_id    Year                    movie_name
0         0  2003.0               Dinosaur Planet
1         1  2004.0    Isle of Man TT 2004 Review
2         2  1997.0                     Character
3         3  1994.0  Paula Abdul's Get Up & Dance
4         4  2004.0      The Rise and Fall of ECW

<a name='3'></a>
## 3 - Exploratory Data Analysis (EDA)

In [4]:
data = movie_titles['Year'].value_counts().sort_index()

trace = go.Scatter(x = data.index,
                   y = data.values,
                   marker = dict(color = '#db0000'))

layout = dict(title = '{} Movies Grouped By Year Of Release'.format(movie_titles.shape[0]),
              xaxis = dict(title = 'Release Year'),
              yaxis = dict(title = 'Movies'),
              template='plotly_white')

fig = go.Figure(data=[trace], layout=layout)
fig.show()

In [11]:
data = df['rating'].value_counts().sort_index(ascending=False)

trace = go.Bar(x = data.index,
               width=0.5,
               text = ['{:.1f} %'.format(val) for val in (data.values / df.shape[0] * 100)],
               textposition = 'outside',
               textangle=0,
               textfont = dict(color = '#000000'),
               y = data.values)

layout = dict(title = 'Distribution Of {} Netflix-Ratings'.format(df.shape[0]),
              xaxis = dict(title = 'Rating'),
              yaxis = dict(title = 'Count'),
              template='simple_white',
              width = 800, 
              height= 500)

fig = go.Figure(data=[trace], layout=layout)
fig.show()

In [12]:
data = df['date'].value_counts()
data.index = pd.to_datetime(data.index)
data.sort_index(inplace=True)

trace = go.Scatter(x = data.index,
                   y = data.values,
                   marker = dict(color = '#db0000'))

layout = dict(title = '{} Movie-Ratings Grouped By Day'.format(df.shape[0]),
              xaxis = dict(title = 'Date'),
              yaxis = dict(title = 'Ratings'),
              template='plotly_white')

fig = go.Figure(data=[trace], layout=layout)
fig.show()

In [16]:
##### Ratings Per Movie #####

data = df.groupby('movie_id')['rating'].count().clip(upper=18000)

trace = go.Histogram(x = data.values,
                     name = 'rating',
                     xbins = dict(start = 0,
                                  end = 18000,
                                  size = 100),
                     marker = dict(color = '#ff7f0e'))

layout = go.Layout(title = 'Distribution Of Rated movie (Clipped at 18000)',
                   xaxis = dict(title = 'No. of rated Movies'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2,
                   template='plotly_white')

fig = go.Figure(data=[trace], layout=layout)
fig.show()



##### Ratings Per User #####

data = df.groupby('user_id')['rating'].count().clip(upper=300)

trace = go.Histogram(x = data.values,
                     name = 'rating',
                     xbins = dict(start = 0,
                                  end = 300,
                                  size = 2),
                     marker = dict(color = '#17becf'))

layout = go.Layout(title = 'Distribution Of Rated-Movies Per Users (Clipped at 300)',
                   xaxis = dict(title = 'No. of rated Movies'),
                   yaxis = dict(title = 'No. of Users'),
                   bargap = 0.2,
                   template='plotly_white')

fig = go.Figure(data=[trace], layout=layout)
fig.show()

<a name='4'></a>
## 4 - Create Train- and Testset

To reduce the dimensionality of the dataset and high computational cost I filter rarely rated movies and rarely rating users out.

In [4]:
# Filter sparse movies
min_movie_ratings = 53000
filter_movies = (df['movie_id'].value_counts()>min_movie_ratings)
filter_movies = filter_movies[filter_movies].index.tolist()

# Filter sparse users
min_user_ratings = 830
filter_users = (df['user_id'].value_counts()>min_user_ratings)
filter_users = filter_users[filter_users].index.tolist()

# Actual filtering
df_filterd = df[(df['movie_id'].isin(filter_movies)) & (df['user_id'].isin(filter_users))]
del filter_movies, filter_users, min_movie_ratings, min_user_ratings
print('Shape User-Ratings unfiltered:\t{}'.format(df.shape))
print('Shape User-Ratings filtered:\t{}'.format(df_filterd.shape))

Shape User-Ratings unfiltered:	(100480507, 4)
Shape User-Ratings filtered:	(6665165, 4)


In [5]:
df_filterd = df_filterd.drop(columns=['date'])

# shuffle & split into train and test
df_filterd = df_filterd.sample(frac=1).reset_index(drop=True)
cutoff = int(0.8*len(df_filterd))
train = df_filterd.iloc[:cutoff]
test = df_filterd.iloc[cutoff:]

<a name='5'></a>
## 5 - Creating Sparse Matrix

In [6]:
# Create a user-movie matrix with empty values
train_sparse = train.pivot_table(index='user_id', columns='movie_id', values='rating')
print('Shape User-Movie-Matrix:\t{}'.format(train_sparse.shape))
train_sparse.sample(3)

Shape User-Movie-Matrix:	(20790, 463)


movie_id  29     174    190    196    298    311    312    328    356    \
user_id                                                                   
897732      NaN    5.0    5.0    5.0    4.0    4.0    5.0    5.0    NaN   
1862272     2.0    NaN    4.0    NaN    NaN    2.0    NaN    3.0    NaN   
672012      4.0    NaN    3.0    NaN    3.0    3.0    4.0    NaN    3.0   

movie_id  456    ...  17354  17386  17404  17430  17440  17478  17559  17621  \
user_id          ...                                                           
897732      NaN  ...    5.0    NaN    5.0    NaN    3.0    4.0    5.0    4.0   
1862272     NaN  ...    3.0    NaN    NaN    NaN    NaN    NaN    4.0    NaN   
672012      3.0  ...    3.0    NaN    3.0    NaN    3.0    NaN    3.0    NaN   

movie_id  17626  17763  
user_id                 
897732      NaN    4.0  
1862272     NaN    NaN  
672012      4.0    NaN  

[3 rows x 463 columns]

<a name='6'></a>
## 6 - Recommendation Engines

<a name='ex-3'></a>
### 6 - 1  Cosine Similarity

In [7]:
# User index for recommendation
user_index = 0

# Number of similar users for recommendation
n_recommendation = 100

# Plot top n recommendations
n_plot = 10


# Fill in missing values
train_imputed = train_sparse.T.fillna(train_sparse.mean(axis=1)).T

# Compute similarity between all users
similarity = cosine_similarity(train_imputed.values)

# Remove self-similarity from similarity-matrix
similarity -= np.eye(similarity.shape[0])


# Sort similar users by index
similar_user_index = np.argsort(similarity[user_index])[::-1]
# Sort similar users by score
similar_user_score = np.sort(similarity[user_index])[::-1]


# Get unrated movies
unrated_movies = train_sparse.iloc[user_index][train_sparse.iloc[user_index].isna()].index

# Weight ratings of the top n most similar users with their rating and compute the mean for each movie
mean_movie_recommendations = (train_imputed.iloc[similar_user_index[:n_recommendation]].T * similar_user_score[:n_recommendation]).T.mean(axis=0)

# Filter for unrated movies and sort results
best_movie_recommendations = mean_movie_recommendations[unrated_movies].sort_values(ascending=False).to_frame().join(movie_titles)


# Create user-id mapping
user_id_mapping = {id:i for i, id in enumerate(train_imputed.index)}

prediction = []
# Iterate over all testset items
for user_id in test['user_id'].unique():
    
    # Sort similar users by index
    similar_user_index = np.argsort(similarity[user_id_mapping[user_id]])[::-1]
    # Sort similar users by score
    similar_user_score = np.sort(similarity[user_id_mapping[user_id]])[::-1]
    
    for movie_id in test[test['user_id']==user_id]['movie_id'].values:

        # Compute predicted score
        score = (train_imputed.iloc[similar_user_index[:n_recommendation]][movie_id] * similar_user_score[:n_recommendation]).values.sum() / similar_user_score[:n_recommendation].sum()
        prediction.append([user_id, movie_id, score])
        


In [8]:

# Create prediction DataFrame
df_pred = pd.DataFrame(prediction, columns=['user_id', 'movie_id', 'Prediction']).set_index(['user_id', 'movie_id'])
df_pred = test.set_index(['user_id', 'movie_id']).join(df_pred)


# Get labels and predictions
y_true = df_pred['rating'].values
y_pred = df_pred['Prediction'].values

# Compute RMSE
rmse = np.sqrt(mean_squared_error(y_true=y_true, y_pred=y_pred))

In [9]:

# Create trace
trace = go.Bar(x = best_movie_recommendations.iloc[:n_plot, 0],
               text = best_movie_recommendations['movie_name'],
               textposition = 'inside',
               textfont = dict(color = '#000000'),
               orientation = 'h',
               y = list(range(1, n_plot+1)),
               marker = dict(color = '#db0000'))
# Create layout
layout = dict(title = 'Ranking Of Top {} Recommended Movies For A User Based On Cosine Similarity: {:.4f} RMSE'.format(n_plot, rmse),
              xaxis = dict(title = 'Recommendation-Rating', range = (4.56, 4.66)),
              yaxis = dict(title = 'Movie'),
              template='simple_white')

fig = go.Figure(data=[trace], layout=layout)
fig.show()

<a name='ex-4'></a>
### 6 - 2 Autoencoders (AutoRec)

In [10]:
users = train["user_id"].unique()
movies = train["movie_id"].unique()
shape = (len(users), len(movies))

# Create indices for users and movies
user_cat = CategoricalDtype(categories=users, ordered=False)
movie_cat = CategoricalDtype(categories=movies, ordered=False)
user_index = train["user_id"].astype(user_cat).cat.codes
movie_index = train["movie_id"].astype(movie_cat).cat.codes

# Conversion via COO matrix
coo = sparse.coo_matrix((train["rating"], (user_index, movie_index)), shape=shape)
csr = coo.tocsr()
mask = (csr > 0)

users_t = test["user_id"].unique()
movies_t = test["movie_id"].unique()
shape_t = (len(users_t), len(movies_t))

# Create indices for users and movies
user_cat_t = CategoricalDtype(categories=users_t, ordered=False)
movie_cat_t = CategoricalDtype(categories=movies_t, ordered=False)
user_index_t = test["user_id"].astype(user_cat_t).cat.codes
movie_index_t = test["movie_id"].astype(movie_cat_t).cat.codes

# Conversion via COO matrix
coo_t = sparse.coo_matrix((test["rating"], (user_index_t, movie_index_t)), shape=shape_t)
csr_t = coo_t.tocsr()
mask_t = (csr_t > 0)

In [11]:
# config
batch_size = 512
epochs = 5
reg = 0.01

mask = (csr > 0) * 1.0
mask_test = (csr_t > 0) * 1.0

# make copies since we will shuffle
A_copy = csr.copy()
mask_copy = mask.copy()
A_test_copy = csr_t.copy()
mask_test_copy = mask_test.copy()

N, M = csr.shape
print("N:", N, "M:", M)
print("N // batch_size:", N // batch_size)

# center the data
mu = csr.sum() / mask.sum()
print("mu:", mu)



# build the model - just a 1 hidden layer autoencoder
i = Input(shape=(M,))
x = Dropout(0.2)(i)
x = Dense(700, activation='relu', kernel_regularizer=l2(reg))(x)
x = BatchNormalization()(x)
x = Dense(128, activation='relu', kernel_regularizer=l2(reg))(x)
x = Dropout(0.2)(x)
x = Dense(M, kernel_regularizer=l2(reg))(x)



def custom_loss(y_true, y_pred):
  mask = K.cast(K.not_equal(y_true, 0), dtype='float32')
  diff = y_pred - y_true
  sqdiff = diff * diff * mask
  sse = K.sum(K.sum(sqdiff))
  n = K.sum(K.sum(mask))
  return sse / n


def generator(csr, M):
  while True:
    for i in range(csr.shape[0] // batch_size + 1):
      upper = min((i+1)*batch_size, csr.shape[0])
      a = csr[i*batch_size:upper].toarray()
      m = M[i*batch_size:upper].toarray()
      a = a - mu * m # must keep zeros at zero!
      noisy = a # no noise
      yield noisy, a


def test_generator(csr, M, csr_t, M_test):
  # assumes A and A_test are in corresponding order
  # both of size N x M
  while True:
    for i in range(csr.shape[0] // batch_size + 1):
      upper = min((i+1)*batch_size, csr.shape[0])
      a = csr[i*batch_size:upper].toarray()
      m = M[i*batch_size:upper].toarray()
      at = csr_t[i*batch_size:upper].toarray()
      mt = M_test[i*batch_size:upper].toarray()
      a = a - mu * m
      at = at - mu * mt
      yield a, at


model = Model(i, x)
model.compile(
  loss=custom_loss,
  optimizer=SGD(learning_rate=0.08, momentum=0.9)
)


result = model.fit(
  generator(csr, mask),
  validation_data=test_generator(A_copy, mask_copy, A_test_copy, mask_test_copy),
  epochs=epochs,
  steps_per_epoch=csr.shape[0] // batch_size + 1,
  validation_steps=csr_t.shape[0] // batch_size + 1,
)

N: 20790 M: 463
N // batch_size: 40
mu: 3.650377747587644
Epoch 1/5
41/41 [==============================] - 3s 46ms/step - loss: 7.5642 - val_loss: 4.1615
Epoch 2/5
41/41 [==============================] - 2s 43ms/step - loss: 2.3572 - val_loss: 1.8002
Epoch 3/5
41/41 [==============================] - 2s 43ms/step - loss: 1.1050 - val_loss: 1.3184
Epoch 4/5
41/41 [==============================] - 2s 43ms/step - loss: 0.8418 - val_loss: 1.2219
Epoch 5/5
41/41 [==============================] - 2s 44ms/step - loss: 0.7859 - val_loss: 1.2031


In [12]:
trace1 = go.Scatter(x=result.epoch,
                   y=result.history['loss'],
                   name = 'train_avg_sse',
                   marker = dict(color = '#db0000'))

trace2 = go.Scatter(x=result.epoch,
                     y=result.history['val_loss'],
                     name = 'val_avg_sse',
                     marker = dict(color = '#17becf'))

layout = dict(title = 'Recommendation with Autoencoders',
              xaxis = dict(title = 'epochs'),
              yaxis = dict(title = 'Movies'),
              template='simple_white')

fig = go.Figure(data=[trace1, trace2], layout=layout)
fig.show()

<a name='ex-5'></a>
### 6 - 3 Matrix Factorisation

Further recommendation engines have less computational cost than the previous one, so I filtered fewer users and movies.

In [13]:
# Filter sparse movies
min_movie_ratings = 10000
filter_movies = (df['movie_id'].value_counts()>min_movie_ratings)
filter_movies = filter_movies[filter_movies].index.tolist()

# Filter sparse users
min_user_ratings = 230
filter_users = (df['user_id'].value_counts()>min_user_ratings)
filter_users = filter_users[filter_users].index.tolist()

# Actual filtering
df_filterd = df[(df['movie_id'].isin(filter_movies)) & (df['user_id'].isin(filter_users))]
del filter_movies, filter_users, min_movie_ratings, min_user_ratings
print('Shape User-Ratings unfiltered:\t{}'.format(df.shape))
print('Shape User-Ratings filtered:\t{}'.format(df_filterd.shape))

Shape User-Ratings unfiltered:	(100480507, 4)
Shape User-Ratings filtered:	(57503076, 4)


In [14]:
df_filterd = df_filterd.drop(columns=['date'])

# shuffle & split into train and test
df_filterd = df_filterd.sample(frac=1).reset_index(drop=True)
cutoff = int(0.8*len(df_filterd))
train = df_filterd.iloc[:cutoff]
test = df_filterd.iloc[cutoff:]

In [15]:
# Create user- & movie-id mapping
user_id_mapping = {id:i for i, id in enumerate(df_filterd['user_id'].unique())}
movie_id_mapping = {id:i for i, id in enumerate(df_filterd['movie_id'].unique())}


# Create correctly mapped train- & testset
train_user_data = train['user_id'].map(user_id_mapping)
train_movie_data = train['movie_id'].map(movie_id_mapping)

test_user_data = test['user_id'].map(user_id_mapping)
test_movie_data = test['movie_id'].map(movie_id_mapping)


N = len(train["user_id"].unique())             # number of users
M = len(train["movie_id"].unique())            # number of movies

# initialize variables
K = 10 # latent dimensionality
mu = train.rating.mean()
epochs = 5
reg = 0.02

##### Create model

u = Input(shape=(1,))  # (none, 1)
m = Input(shape=(1,))

# Create embedding layers for users and movies
u_embedding = Embedding(N, K, embeddings_regularizer=l2(reg))(u) # (none, 1, K)
m_embedding = Embedding(M, K, embeddings_regularizer=l2(reg))(m) # (none, 1, K)

u_bias = Embedding(N, 1)(u) # (none, 1, 1)
m_bias = Embedding(M, 1)(m) # (none, 1, 1)
x = Dot(axes=2)([u_embedding, m_embedding]) # (none, 1, 1)

x = Add()([x, u_bias, m_bias])
x = Flatten()(x)                     # (none, 1)

model = Model(inputs=[u, m], outputs=x)
model.compile(
              loss='mse',
              optimizer=SGD(learning_rate=0.08, momentum=0.9)
              )

result = model.fit(
                    x=[train_user_data, train_movie_data],
                    y=train.rating - mu,
                    epochs=epochs,
                    batch_size=1024,
                    validation_data=(
                        [test_user_data, test_movie_data],
                        test.rating - mu
                    )
)

Epoch 1/5
44925/44925 [==============================] - 715s 16ms/step - loss: 0.9056 - val_loss: 0.8500
Epoch 2/5
44925/44925 [==============================] - 693s 15ms/step - loss: 0.8307 - val_loss: 0.8201
Epoch 3/5
44925/44925 [==============================] - 729s 16ms/step - loss: 0.8116 - val_loss: 0.8094
Epoch 4/5
44925/44925 [==============================] - 847s 19ms/step - loss: 0.8041 - val_loss: 0.8050
Epoch 5/5
44925/44925 [==============================] - 863s 19ms/step - loss: 0.8007 - val_loss: 0.8031


In [16]:
# plot mse
trace1 = go.Scatter(x=result.epoch,
                   y=result.history['loss'],
                   name = 'train_mse',
                   marker = dict(color = '#db0000'))

trace2 = go.Scatter(x=result.epoch,
                     y=result.history['val_loss'],
                     name = 'val_mse',
                     marker = dict(color = '#17becf'))

layout = dict(title = 'Matrix Factorization in Keras',
              xaxis = dict(title = 'epochs'),
              yaxis = dict(title = 'Movies'),
              template='simple_white')

fig = go.Figure(data=[trace1, trace2], layout=layout)
fig.show()

<a name='ex-6'></a>
### 6 - 4  Deep Learning With Keras

In [17]:

# Create user- & movie-id mapping
user_id_mapping = {id:i for i, id in enumerate(df_filterd['user_id'].unique())}
movie_id_mapping = {id:i for i, id in enumerate(df_filterd['movie_id'].unique())}

# keras model
u = Input(shape=(1,))
m = Input(shape=(1,))
u_embedding = Embedding(N, K)(u) # (None, 1, K)
m_embedding = Embedding(M, K)(m) # (None, 1, K)
u_embedding = Flatten()(u_embedding) # (None, K)
m_embedding = Flatten()(m_embedding) # (None, K)
x = Concatenate()([u_embedding, m_embedding]) # (None, 2K)

# the neural network
x = Dense(512)(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = Dropout(0.5)(x)
x = Dense(128)(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = Dense(1)(x)

model = Model(inputs=[u, m], outputs=x)
model.compile(
              loss='mse',
              optimizer=SGD(learning_rate=0.08, momentum=0.9)
)

result = model.fit(
              x=[train_user_data, train_movie_data],
              y=train.rating - mu,
              epochs=epochs,
              batch_size=1024,
              validation_data=(
              [test_user_data, test_movie_data],
              test.rating - mu
  )
)

Epoch 1/5
44925/44925 [==============================] - 1496s 33ms/step - loss: 0.7953 - val_loss: 0.7405
Epoch 2/5
44925/44925 [==============================] - 1138s 25ms/step - loss: 0.7332 - val_loss: 0.7202
Epoch 3/5
44925/44925 [==============================] - 1130s 25ms/step - loss: 0.7127 - val_loss: 0.7053
Epoch 4/5
44925/44925 [==============================] - 1127s 25ms/step - loss: 0.6969 - val_loss: 0.7046
Epoch 5/5
44925/44925 [==============================] - 1152s 26ms/step - loss: 0.6856 - val_loss: 0.7194


In [18]:
trace1 = go.Scatter(x=result.epoch,
                   y=result.history['loss'],
                   name = 'train_mse',
                   marker = dict(color = '#db0000'))

trace2 = go.Scatter(x=result.epoch,
                     y=result.history['val_loss'],
                     name = 'val_mse',
                     marker = dict(color = '#17becf'))

layout = dict(title = 'Deep Neural Network',
              xaxis = dict(title = 'epochs'),
              yaxis = dict(title = 'Movies'),
              template='simple_white')

fig = go.Figure(data=[trace1, trace2], layout=layout)
fig.show()

<a name='ex-7'></a>
### 6 - 5  Residual Learning

In [19]:
##### Residual Learning

# keras model
u = Input(shape=(1,))
m = Input(shape=(1,))
u_embedding = Embedding(N, K)(u) # (None, 1, K)
m_embedding = Embedding(M, K)(m) # (None, 1, K)


##### main branch
u_bias = Embedding(N, 1)(u) # (None, 1, 1)
m_bias = Embedding(M, 1)(m) # (None, 1, 1)
x = Dot(axes=2)([u_embedding, m_embedding]) # (None, 1, 1)
x = Add()([x, u_bias, m_bias])
x = Flatten()(x) # (None, 1)


##### side branch
u_embedding = Flatten()(u_embedding) # (None, K)
m_embedding = Flatten()(m_embedding) # (None, K)
y = Concatenate()([u_embedding, m_embedding]) # (None, 2K)
y = Dense(512)(y)
y = BatchNormalization()(y)
y = Activation('relu')(y)
y = Dropout(0.5)(y)
y = Dense(128)(x)
y = BatchNormalization()(y)
y = Activation('relu')(y)
y = Dense(1)(y)


##### merge
x = Add()([x, y])

model = Model(inputs=[u, m], outputs=x)
model.compile(
              loss='mse',
              optimizer=SGD(lr=0.08, momentum=0.9)
)

result = model.fit(
              x=[train_user_data, train_movie_data],
              y=train.rating - mu,
              epochs=epochs,
              batch_size=1024,
              validation_data=(
              [test_user_data, test_movie_data],
              test.rating - mu
  )
)

C:\ProgramData\Anaconda3\lib\site-packages\keras\optimizer_v2\gradient_descent.py:102: UserWarning:

The `lr` argument is deprecated, use `learning_rate` instead.



Epoch 1/5
44925/44925 [==============================] - 255s 6ms/step - loss: 0.8274 - val_loss: 0.8066
Epoch 2/5
44925/44925 [==============================] - 259s 6ms/step - loss: 0.7775 - val_loss: 0.7471
Epoch 3/5
44925/44925 [==============================] - 258s 6ms/step - loss: 0.7266 - val_loss: 0.7139
Epoch 4/5
44925/44925 [==============================] - 258s 6ms/step - loss: 0.6926 - val_loss: 0.6878
Epoch 5/5
44925/44925 [==============================] - 262s 6ms/step - loss: 0.6654 - val_loss: 0.6698


In [31]:
trace1 = go.Scatter(x=result.epoch,
                   y=result.history['loss'],
                   name = 'train_mse',
                   marker = dict(color = '#db0000'))

trace2 = go.Scatter(x=result.epoch,
                     y=result.history['val_loss'],
                     name = 'val_mse',
                     marker = dict(color = '#17becf'))

layout = dict(title = 'Residual Learning',
              xaxis = dict(title = 'epochs'),
              yaxis = dict(title = 'Movies'),
              template='simple_white')

fig = go.Figure(data=[trace1, trace2], layout=layout)
fig.show()

ValueError: 
Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido
